# Posterior probabilities and Likelyhoods for origin based on word pronunciation

Tables with the posterior probabilities and likelihoods of *being from a region* based on the *stated pronunciation of one specific word*

In [13]:
import sys
sys.path.append('..')

from stimmen.cbs import province_geojson, gwb_in_province

import pandas
import MySQLdb
import numpy
import json

db = MySQLdb.connect(user='root', passwd='Nmmxhjgt1@', db='stimmen')

from matplotlib import pyplot
import folium
from IPython.display import display
from shapely.geometry import Polygon, MultiPolygon, shape, Point
from jupyter_progressbar import ProgressBar
from collections import defaultdict
from ipy_table import make_table

In [7]:
gemeentes = gwb_in_province('Friesland', region_level='gem', region_year=2018)

In [11]:
gemeente_shapes = [shape(feature['geometry']) for feature in gemeentes['features']]
gemeente_names = [feature['properties']['GM_NAAM'] for feature in gemeentes['features']]

def get_gemeente(point):
    for i, shape_ in enumerate(gemeente_shapes):
        if shape_.contains(point):
            return i
    return -1

In [14]:
# Answers to how participants state a word should be pronounces.

answers = pandas.read_sql('''
SELECT prediction_quiz_id, user_lat, user_lng, question_text, answer_text
FROM       core_surveyresult as survey
INNER JOIN core_predictionquizresult as result ON survey.id = result.survey_result_id
INNER JOIN core_predictionquizresultquestionanswer as answer
    ON result.id = answer.prediction_quiz_id
''', db)

In [15]:
# Takes approximately 2 minutes

gemeente_map = {
    (lng, lat): get_gemeente(Point(lng, lat))
    for lng, lat in set(zip(answers['user_lng'], answers['user_lat']))
}

answers['gemeente'] = [
    gemeente_map[(lng, lat)]
    for lat, lng in zip(answers['user_lat'], answers['user_lng'])
]

# Posterior probability

Probability for a gemeente given a specific pronunciation.

In [6]:
colors = pyplot.get_cmap('tab20').colors

for question, rows in answers.groupby('question_text'):
    answer_texts = set(rows['answer_text'])
    print(question)
    display(make_table(
        [['', 'support', 'entropy'] + gemeente_names] + [
            [
                answer_text, summed,
                sum(
                    -numpy.log(p) * p
                    for gemeente, count in counts.items()
                    if gemeente >= 0
                    for p in [count / summed if summed > 0 else 0] # alias
            )] + [
                '%d%%' % percentage if percentage > 0 else ''
                for gemeente, gemeente_name in enumerate(gemeente_names)
                for percentage in [round(100 * counts[gemeente] / summed) if summed > 0 else 0] # alias
            ]
            for answer_text, rows_ in rows.groupby('answer_text')
            
            for counts in [defaultdict(lambda: 0, rows_['gemeente'][rows_['gemeente'] >= 0].value_counts())] # alias
            for summed in [sum(counts.values())] # alias
        ]
    ))

"armen" (*lichaamsdeel)


"avond"


"bij" (*insect)


"blad" (aan een boom)


"borst" (*lichaamsdeel)


...

oog


tand


trein


vis


zaterdag


# Likelyhoods

Probabilty of a pronunciation given that someone is from a municipality

In [52]:
for question, rows in answers.groupby('question_text'):
    answer_texts = set(rows['answer_text'])
    print(question)
    display(make_table(
        [[''] + list(answer_texts)] + [
            [gemeente_names[gemeente]] + [
                percentage if percentage > 0 else ''
                for answer_text in answer_texts
                for percentage in [round(100 * counts[answer_text] / summed)] # alias
            ]
            for gemeente, rows_ in rows.groupby('gemeente')
            if gemeente >= 0
            for counts in [defaultdict(lambda: 0, rows_['answer_text'].value_counts())] # alias
            for summed in [len(rows_)] # alias
        ]
    ))

"armen" (*lichaamsdeel)


"avond"


"bij" (*insect)


"blad" (aan een boom)


"borst" (*lichaamsdeel)


...

oog


tand


trein


vis


zaterdag
